
# 使用 OSMnx 的 OpenStreetMap

这个示例展示了如何使用 OSMnx 从 OpenStreetMap 下载和建模街道网络，可视化中心性，然后将图保存为 GeoPackage 或 GraphML 文件。

OSMnx 是一个 Python 包，用于从 OpenStreetMap 下载、建模、分析和可视化街道网络及其他地理空间特征。你可以用一行代码下载和建模步行、驾驶或骑行网络，然后轻松地分析和可视化它们。你同样可以轻松地处理城市便利设施/兴趣点、建筑轮廓、交通站点、高程数据、街道方向、速度/行程时间以及路径规划。

请参阅 https://osmnx.readthedocs.io 获取 OSMnx 文档。
请参阅 https://github.com/gboeing/osmnx-examples 获取 OSMnx 示例图库。


In [ ]:
import networkx as nx
import osmnx as ox

ox.settings.use_cache = True

# 从OSM下载街道网络数据并构建一个MultiDiGraph模型
G = ox.graph.graph_from_point((37.79, -122.41), dist=750, network_type="drive")

# 估算边缘（驾驶）速度并计算边缘行程时间
G = ox.speed.add_edge_speeds(G)
G = ox.speed.add_edge_travel_times(G)

# 你可以将MultiDiGraph转换为GeoPandas GeoDataFrames，反之亦然
gdf_nodes, gdf_edges = ox.utils_graph.graph_to_gdfs(G)
G = ox.utils_graph.graph_from_gdfs(gdf_nodes, gdf_edges, graph_attrs=G.graph)

# 将 MultiDiGraph 转换为 DiGraph 以使用 nx.betweenness_centrality 函数
# 通过最小化travel_time属性值来选择平行边
D = ox.utils_graph.get_digraph(G, weight="travel_time")

# 计算节点介数中心性，按旅行时间加权
bc = nx.betweenness_centrality(D, weight="travel_time", normalized=True)
nx.set_node_attributes(G, values=bc, name="bc")

# 绘制图形，根据介数中心性为节点着色
nc = ox.plot.get_node_colors_by_attr(G, "bc", cmap="plasma")
fig, ax = ox.plot.plot_graph(
    G, bgcolor="k", node_color=nc, node_size=50, edge_linewidth=2, edge_color="#333333"
)

# 将图保存为GeoPackage或GraphML文件
ox.io.save_graph_geopackage(G, filepath="./graph.gpkg")
ox.io.save_graphml(G, filepath="./graph.graphml")